# Crawling from paperswithcode.com

[API Documentation](https://paperswithcode.com/api/v1/docs/)

In [1]:
import pandas as pd
import requests
from tqdm.notebook import trange, tqdm
import plotly.express as px
import uuid
from sentence_transformers import SentenceTransformer
from umap import UMAP
from sklearn.model_selection import train_test_split

/mnt/nvme01/.venv/lib/python3.11/site-packages/umap/distances.py:1063: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
/mnt/nvme01/.venv/lib/python3.11/site-packages/umap/distances.py:1071: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
/mnt/nvme01/.venv/lib/python3.11/site-packages/umap/distances.py:1086: NumbaDeprecationWarning: The 'nop

In [ ]:
# RUN ONLY IF YOU DONT HAVE THE CORRESPONDING JSON FILES AT HAND - it takes around 2 hours to run

ITEMS_PER_PAGE = 100

# Get all areas
print("Getting all areas...")
areas = requests.get("https://paperswithcode.com/api/v1/areas").json()
areas = pd.DataFrame(areas["results"])
print("Done.")

# Get all tasks from all areas and write them to the datafile
print("Getting all tasks...")
# Make a new column tasks
areas["tasks"] = areas.id.apply(lambda x: [])
page = 1
for area_id in tqdm(areas.id):
    # Make a first request to get the count
    count = requests.get(f"https://paperswithcode.com/api/v1/areas/{area_id}/tasks?items_per_page=1").json()["count"]
    print(f"Getting tasks from area {area_id}. Got {count} tasks...")
    for page in trange(1, int(count / ITEMS_PER_PAGE) + 2):
        try:
            response = requests.get(f"https://paperswithcode.com/api/v1/areas/{area_id}/tasks?items_per_page={ITEMS_PER_PAGE}&page={page}").json()
            # Append the results to a list in a new tasks column
            if response["results"] is not None:
                areas.loc[areas.id == area_id, "tasks"] = areas.loc[areas.id == area_id, "tasks"].apply(lambda x: x + response["results"])
            else:
                print(f"Error getting tasks from area {area_id}.")
                break

            page += 1
        except Exception as e:
            print(f"Error getting tasks from area {area_id}.")
            print(e)
            print(response)
print("Done.")

# Write areas to json file
areas.to_json("areas.json", orient="records")

print(f"Saved {len(areas)} areas with corresponding tasks to areas.json.")

In [ ]:
# RUN ONLY IF YOU DONT HAVE THE CORRESPONDING JSON FILES AT HAND - it takes around 2 hours to run

# Get areas.json
areas = pd.read_json("areas.json", orient="records")

# Get all papers from all tasks and write them to the dataframe
print("Getting all papers...")
page = 1
for area_id in tqdm(areas.id):
    print(f"Getting papers from area {area_id} with {len(areas.loc[areas.id == area_id, 'tasks'].values[0])} tasks...")
    for task_id in trange(len(areas.loc[areas.id == area_id, "tasks"].values[0])):
        count = requests.get(f"https://paperswithcode.com/api/v1/tasks/{areas.loc[areas.id == area_id, 'tasks'].values[0][task_id]['id']}/papers?items_per_page=1").json()["count"]
        # for page in trange(1, int(count / ITEMS_PER_PAGE) + 2): # If you want to see the progress of each task
        for page in range(1, int(count / ITEMS_PER_PAGE) + 2):
            try:
                response = requests.get(f"https://paperswithcode.com/api/v1/tasks/{areas.loc[areas.id == area_id, 'tasks'].values[0][task_id]['id']}/papers?items_per_page={ITEMS_PER_PAGE}&page={page}").json()
                if response["results"] is not None:
                    # Write the papers in the corresponding tasks
                    areas.loc[areas.id == area_id, 'tasks'].values[0][task_id]["papers"] = response["results"]                
                else:
                    print(f"Error getting papers from task {areas.loc[areas.id == area_id, 'tasks'].values[0][task_id]['id']}.")
                    break
                page += 1
            except Exception as e:
                print(f"Error getting papers from task {areas.loc[areas.id == area_id, 'tasks'].values[0][task_id]['id']}.")
                print(e)
                print(response)
                
print("Done.")

# Write areas to json file
areas.to_json("areas_tasks_papers.json", orient="records")
print(f"Saved {len(areas)} areas with corresponding tasks and papers to areas_tasks_papers.json.")

# Exploring the Data

Now we have a look at the gathered areas, tasks and papers from paperswithcode.com. We will use plotly express to visualize the data.

In [2]:
print("EXPLORING THE DATA")

# Get areas_tasks_papers.json
working_df = pd.read_json("areas_tasks_papers.json", orient="records")

## TASKS PER AREA

# Get the total amount of tasks per area
working_df["total_tasks"] = working_df.tasks.apply(lambda x: len(x))

# Sort the areas by the total amount of tasks
working_df = working_df.sort_values(by="total_tasks", ascending=False)

# Plot the areas
fig = px.bar(working_df, x="name", y="total_tasks", title="Total amount of tasks per area")
fig.update_traces(marker_color='rgb(255, 20, 0)')
fig.show()

## PAPERS PER AREA

# Get the total amount of papers per area
working_df["total_papers"] = working_df.tasks.apply(lambda x: sum([len(task["papers"]) for task in x]))

# Sort the areas by the total amount of papers
working_df = working_df.sort_values(by="total_papers", ascending=False)

# Plot the areas
fig = px.bar(working_df, x="name", y="total_papers", title="Total amount of papers per area")
fig.show()

print(f"There are in total {working_df.total_papers.sum()} papers over {working_df.total_tasks.sum()} tasks in {len(working_df)} areas.")

EXPLORING THE DATA


There are in total 72518 papers over 3059 tasks in 16 areas.


# Data Preprocessing and Embedding.

Data wrangling, title + abstract embedding and CSV export for Neo4j.

In [3]:
### BUILDING NODES AND RELATIONSHIPS FOR THE NEO4J GRAPH DATABASE ###

# Get areas_tasks_papers.json
working_df = pd.read_json("areas_tasks_papers.json", orient="records")

## AREAS NODES ##
print("Building areas csv...")
areas_df = working_df.copy()
areas_df.drop(columns=["tasks"], inplace=True)
areas_df.rename(columns={"id": "pwc_id", "name": "title"}, inplace=True)
areas_df["areaID"] = areas_df.pwc_id.apply(lambda x: str(uuid.uuid4()))
areas_df = areas_df[["areaID", "pwc_id", "title"]]

## TASKS NODES ##
print("Building tasks csv...")
tasks_list = [
    {
        "taskID": str(uuid.uuid4()),
        "pwc_id": task["id"],
        "title": task["name"],
        "description": task["description"],
        "areaID": area_id
    }
    for area_id in tqdm(areas_df.pwc_id)
    for task in working_df.loc[working_df.id == area_id, "tasks"].values[0]
]
tasks_df = pd.DataFrame(tasks_list, columns=["taskID", "pwc_id", "title", "description", "areaID"])

## PAPERS NODES ##
print("Building papers csv...")
papers_list = [
    {
        "paperID": str(uuid.uuid4()),
        "pwc_id": paper["id"],
        "arxiv_id": paper["arxiv_id"],
        "nips_id": paper["nips_id"],
        "url_abs": paper["url_abs"],
        "url_pdf": paper["url_pdf"],
        "title": paper["title"],
        "abstract": paper["abstract"],
        "authors": paper["authors"],
        "published": paper["published"],
        "conference": paper["conference"],
        "conference_url_abs": paper["conference_url_abs"],
        "conference_url_pdf": paper["conference_url_pdf"],
        "proceeding": paper["proceeding"],
        "taskID": task["id"],
        "areaID": area_id
    }
    for area_id in tqdm(areas_df.pwc_id)
    for task in working_df.loc[working_df.id == area_id, "tasks"].values[0]
    for paper in task["papers"]
]
papers_df = pd.DataFrame(papers_list, columns=[
    "paperID",
    "pwc_id",
    "arxiv_id",
    "nips_id",
    "url_abs",
    "url_pdf",
    "title",
    "abstract",
    "authors",
    "published",
    "conference",
    "conference_url_abs", 
    "conference_url_pdf",
    "proceeding",
    "taskID",
    "areaID"
])

# Merge all duplicates on the subset of pwc_id and title. Merge the two fields "taskID" and "areaID" into a list. Keep everything else from the first row.
papers_df = papers_df.groupby(["pwc_id", "title"]).agg({
    "paperID": lambda x: list(x)[0],
    "arxiv_id": lambda x: list(x)[0],
    "nips_id": lambda x: list(x)[0],
    "url_abs": lambda x: list(x)[0],
    "url_pdf": lambda x: list(x)[0],
    "abstract": lambda x: list(x)[0],
    "authors": lambda x: list(x)[0],
    "published": lambda x: list(x)[0],
    "conference": lambda x: list(x)[0],
    "conference_url_abs": lambda x: list(x)[0],
    "conference_url_pdf": lambda x: list(x)[0],
    "proceeding": lambda x: list(x)[0],
    "taskID": list,
    "areaID": list
}).reset_index()

# Put the paperID as the first column
papers_df = papers_df[["paperID", "pwc_id", "arxiv_id", "nips_id", "url_abs", "url_pdf", "title", "abstract", "authors", "published", "conference", "conference_url_abs", "conference_url_pdf", "proceeding", "taskID", "areaID"]]

print(f"There are in total {papers_df.shape[0]} papers over {tasks_df.shape[0]} tasks in {areas_df.shape[0]} areas.")

Building areas csv...
Building tasks csv...


  0%|          | 0/16 [00:00<?, ?it/s]

Building papers csv...


  0%|          | 0/16 [00:00<?, ?it/s]

There are in total 55760 papers over 3059 tasks in 16 areas.


In [ ]:
# Load the SciNCL model
model = SentenceTransformer('malteos/scincl')

print("CALCULATING EMBEDDINGS - this can take a while...")
# Calculate the embeddings for the papers
papers_df["embedding"] = papers_df["abstract"].apply(lambda x: model.encode(str(x)))
print("CALCULATING EMBEDDINGS - done!")

In [ ]:
# Perform UMAP Dimensionality Reduction on the embeddings
print("PERFORMING UMAP DIMENSIONALITY REDUCTION - this can take a while...")
umap_embeddings = UMAP(n_neighbors=15, n_components=2, metric='cosine').fit_transform(papers_df["embedding"].tolist())
papers_df["umap_embedding"] = umap_embeddings.tolist()
print("PERFORMING UMAP DIMENSIONALITY REDUCTION - done!")

In [4]:
# Save the dataframes to csv
areas_df.to_csv("areas.csv", index=False)
tasks_df.to_csv("tasks.csv", index=False)
papers_df.to_csv("papers.csv", index=False)

# Split the papers_df in train and test sets (80/20). Use built in pandas function to split the dataframe.
papers_train_df, papers_test_df = train_test_split(papers_df, test_size=0.2, random_state=42)

# Save the dataframes to csv
papers_train_df.to_csv("papers_train.csv", index=False)
papers_test_df.to_csv("papers_test.csv", index=False)

print("Done!")

Done!
